# Load data

Make sure you have .env file in ttools or any parent dir with your Alpaca keys.

```bash
ACCOUNT1_LIVE_API_KEY=api_key
ACCOUNT1_LIVE_SECRET_KEY=secret_key
```

###  Cache directories

Daily trade files - DATADIR/tradecache
Agg data cache - DATADIR/aggcache

`DATADIR` - user_data_dir from appdirs library - see `config.py`

In [1]:
import pandas as pd
import numpy as np
from ttools.utils import AggType
from datetime import datetime
from ttools.aggregator_vectorized import generate_time_bars_nb, aggregate_trades
from ttools.loaders import load_data, prepare_trade_cache
from ttools.utils import zoneNY
import vectorbtpro as vbt
from lightweight_charts import PlotDFAccessor, PlotSRAccessor


vbt.settings.set_theme("dark")
vbt.settings['plotting']['layout']['width'] = 1280
vbt.settings.plotting.auto_rangebreaks = True
# Set the option to display with pagination
pd.set_option('display.notebook_repr_html', True)
pd.set_option('display.max_rows', 10)  # Number of rows per page


TTOOLS: Loaded env variables from file /Users/davidbrazda/Documents/Development/python/.env


# Fetching aggregated data

Available aggregation types: 
- time based bars - AggType.OHLCV
- volume based bars - AggType.OHLCV_VOL, resolution = volume threshold
- dollar based bars - AggType.OHLCV_DOL, resolution = dollar threshold
- renko bars - AggType.OHLCV_RENKO resolution = bricksize

In [6]:
#This is how to call LOAD function
symbol = ["BAC","AAPL"]
#datetime in zoneNY 
day_start = datetime(2024, 10, 14, 9, 45, 0)
day_stop = datetime(2024, 10, 16, 15, 1, 0)
day_start = zoneNY.localize(day_start)
day_stop = zoneNY.localize(day_stop)

#requested AGG
resolution = 12 #12s bars
agg_type = AggType.OHLCV #other types AggType.OHLCV_VOL, AggType.OHLCV_DOL, AggType.OHLCV_RENKO
exclude_conditions = ['C','O','4','B','7','V','P','W','U','Z','F','9','M','6'] #None to defaults
minsize = 100 #min trade size to include
main_session_only = True
force_remote = True

data = load_data(symbol = symbol,
                     agg_type = agg_type,
                     resolution = resolution,
                     start_date = day_start,
                     end_date = day_stop,
                     #exclude_conditions = None,
                     minsize = minsize,
                     main_session_only = main_session_only,
                     force_remote = False,
                     return_vbt = True, #returns vbt object
                     verbose = False
                     )

#basic_data.ohlcv.plot()
data.ohlcv.data[symbol[0]].lw.plot()


Fetching data: 100%|██████████| 3/3 [00:03<00:00,  1.32s/it]
/Users/davidbrazda/Documents/Development/python/ttools/.venv/lib/python3.10/site-packages/vectorbtpro/data/base.py:1905: UserWarning: Symbols have mismatching index. Setting missing data points to NaN.
  data = cls_or_self.align_index(data, missing=missing_index, silence_warnings=silence_warnings)


In [5]:
data.ohlcv.data[symbol[0]]

open    high     low    close   volume
time                                                                
2024-10-14 09:45:00-04:00  41.9650  41.970  41.950  41.9500  17895.0
2024-10-14 09:45:12-04:00  41.9589  41.965  41.950  41.9650   6281.0
2024-10-14 09:45:24-04:00  41.9650  42.005  41.965  41.9975   3522.0
2024-10-14 09:45:36-04:00  41.9900  42.005  41.990  42.0000   5960.0
2024-10-14 09:45:48-04:00  42.0050  42.040  42.005  42.0300   9113.0
...                            ...     ...     ...      ...      ...
2024-10-16 15:00:00-04:00  42.9150  42.915  42.910  42.9100  12872.0
2024-10-16 15:00:12-04:00  42.9150  42.920  42.910  42.9200   7574.0
2024-10-16 15:00:24-04:00  42.9200  42.920  42.910  42.9200   1769.0
2024-10-16 15:00:36-04:00  42.9200  42.920  42.905  42.9050  26599.0
2024-10-16 15:00:48-04:00  42.9050  42.905  42.880  42.8800   9216.0

[5480 rows x 5 columns]

## Prepare daily trade cache
This is how to prepare trade cache for given symbol and period (if daily trades are not cached they are remotely fetched.)

In [8]:
symbols = ["BAC", "AAPL"]
#datetime in zoneNY 
day_start = datetime(2024, 10, 1, 9, 45, 0)
day_stop = datetime(2024, 10, 14, 15, 1, 0)
day_start = zoneNY.localize(day_start)
day_stop = zoneNY.localize(day_stop)
force_remote = False

prepare_trade_cache(symbols, day_start, day_stop, force_remote)

Started for BAC
Contains 10  market days


Fetching data:   0%|          | 0/10 [00:00<?, ?it/s]

Loaded from CACHE /Users/davidbrazda/Library/Application Support/v2realbot/tradecache/BAC-2024-10-01.parquet
filtrujeme 09:45:00 23:59:59.999999
excluding conditions ['4', '6', '7', '9', 'B', 'C', 'F', 'M', 'O', 'P', 'U', 'V', 'W', 'Z']
Loaded from CACHE /Users/davidbrazda/Library/Application Support/v2realbot/tradecache/BAC-2024-10-02.parquet
Loaded from CACHE /Users/davidbrazda/Library/Application Support/v2realbot/tradecache/BAC-2024-10-03.parquet
filtrujeme 00:00:00 23:59:59.999999
excluding conditions ['4', '6', '7', '9', 'B', 'C', 'F', 'M', 'O', 'P', 'U', 'V', 'W', 'Z']
minsize 100
filtrujeme 00:00:00 23:59:59.999999


Fetching data:  10%|█         | 1/10 [00:00<00:07,  1.27it/s]

Loaded from CACHE /Users/davidbrazda/Library/Application Support/v2realbot/tradecache/BAC-2024-10-04.parquet
excluding conditions ['4', '6', '7', '9', 'B', 'C', 'F', 'M', 'O', 'P', 'U', 'V', 'W', 'Z']
filtrujeme 00:00:00 23:59:59.999999
minsize 100


...

minsize 100


Fetching data:  80%|████████  | 8/10 [00:12<00:02,  1.10s/it]

minsize 100
minsize 100


Fetching data: 100%|██████████| 10/10 [00:13<00:00,  1.34s/it]

minsize 100
Finished for AAPL


### Prepare daily trade cache - cli script

Python script prepares trade cache for specified symbols and date range.

Usually 1 day takes about 35s. It is stored in /tradescache/ directory as daily file keyed by symbol.

To run this script in the background with specific arguments:

```bash
# Running without forcing remote fetch
python3 prepare_cache.py --symbols BAC AAPL --day_start 2024-10-14 --day_stop 2024-10-18 &

# Running with force_remote set to True
python3 prepare_cache.py --symbols BAC AAPL --day_start 2024-10-14 --day_stop 2024-10-18 --force_remote &

```